In [73]:
import datetime
from datetime import date
from datetime import datetime
import requests
import pprint
from bs4 import BeautifulSoup
import pandas as pd
import re
import pickle
from urllib.request import urlopen
import glob
# import altair as alt
import time
import itertools
import numpy as np
import operator
from datetime import timedelta

pd.options.display.max_columns = 5000
pd.options.display.max_rows = 5000

In [74]:
# Load Dataset

# Renzo's Path
# dataset = pd.read_csv('/Volumes/GoogleDrive/.shortcut-targets-by-id/1KUGn_35OjAoOP2puz6yG-2g_8LBxvDG_/SIADS 697 - Capstone/Dataframes/complete_final_df.csv')

# Sravan's Path
dataset = pd.read_csv('/Users/srav88/My Drive/SIADS 697 - Capstone/Dataframes/complete_final_df_2.csv')

/Library/Frameworks/Python.framework/Versions/3.8/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3441: DtypeWarning: Columns (43,44,45,46,47,48,50,52,53,54,55,56,58,59,60,61,62,63,64,65,66,67,68,69,70,71,72,73,74,75,76,77,78,79,80,81,83,84,85,86,87,88,89,90,91,93,94,95,100) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


In [76]:
# Creating variable 'was_match' to know which rows are matches (real games) and which rows are not

dataset.loc[dataset['Min'].isnull(), 'was_match'] = 0
dataset.loc[dataset['Min'].isnull() == False, 'was_match'] = 1

In [77]:
# Filling in some missing values

dataset.loc[dataset['name'].isnull(), 'Prog'] = dataset['PlayerName']

# [Min, Gls, Ast, PK, PKatt, Sh, SoT, CrdY, CrdR, Touches, Press, Tkl, Int, Blocks, xG, npxG, xA, SCA, GCA, Prog, Carries, Prog.1, Succ, Att.1, \
# Fls, Off, Crs, TklW, OG, PKwon, PKcon, Won, Loss, Draw] all have 150755 NaN's, of which none are when matches are played, so we equal those \
# NaN's in these variables to 0
dataset.loc[dataset['Min'].isnull(), 'Min'] = 0
dataset.loc[dataset['Gls'].isnull(), 'Gls'] = 0
dataset.loc[dataset['Ast'].isnull(), 'Ast'] = 0
dataset.loc[dataset['PK'].isnull(), 'PK'] = 0
dataset.loc[dataset['PKatt'].isnull(), 'PKatt'] = 0
dataset.loc[dataset['Sh'].isnull(), 'Sh'] = 0
dataset.loc[dataset['SoT'].isnull(), 'SoT'] = 0
dataset.loc[dataset['CrdY'].isnull(), 'CrdY'] = 0
dataset.loc[dataset['CrdR'].isnull(), 'CrdR'] = 0
dataset.loc[dataset['Touches'].isnull(), 'Touches'] = 0
dataset.loc[dataset['Press'].isnull(), 'Press'] = 0
dataset.loc[dataset['Tkl'].isnull(), 'Tkl'] = 0
dataset.loc[dataset['Int'].isnull(), 'Int'] = 0
dataset.loc[dataset['Blocks'].isnull(), 'Blocks'] = 0
dataset.loc[dataset['xG'].isnull(), 'xG'] = 0
dataset.loc[dataset['npxG'].isnull(), 'npxG'] = 0
dataset.loc[dataset['xA'].isnull(), 'xA'] = 0
dataset.loc[dataset['SCA'].isnull(), 'SCA'] = 0
dataset.loc[dataset['GCA'].isnull(), 'GCA'] = 0
dataset.loc[dataset['Prog'].isnull(), 'Prog'] = 0
dataset.loc[dataset['Carries'].isnull(), 'Carries'] = 0
dataset.loc[dataset['Prog.1'].isnull(), 'Prog.1'] = 0
dataset.loc[dataset['Succ'].isnull(), 'Succ'] = 0
dataset.loc[dataset['Att.1'].isnull(), 'Att.1'] = 0
dataset.loc[dataset['Fls'].isnull(), 'Fls'] = 0
dataset.loc[dataset['Off'].isnull(), 'Off'] = 0
dataset.loc[dataset['Crs'].isnull(), 'Crs'] = 0
dataset.loc[dataset['TklW'].isnull(), 'TklW'] = 0
dataset.loc[dataset['OG'].isnull(), 'OG'] = 0
dataset.loc[dataset['PKwon'].isnull(), 'PKwon'] = 0
dataset.loc[dataset['PKcon'].isnull(), 'PKcon'] = 0
dataset.loc[dataset['Won'].isnull(), 'Won'] = 0
dataset.loc[dataset['Loss'].isnull(), 'Loss'] = 0
dataset.loc[dataset['Draw'].isnull(), 'Draw'] = 0

In [78]:
# Assigning Dummy Variables for player position from 'Position:'

dataset.loc[dataset['Position:'].isnull(), 'Position:'] = ''
dataset['defender'] = np.where(dataset['Position:'].str.contains('Defender'), 1, 0)
dataset['attacker'] = np.where(dataset['Position:'].str.contains('attack'), 1, 0)
dataset['midfielder'] = np.where(dataset['Position:'].str.contains('midfield'), 1, 0)
dataset['goalkeeper'] = np.where(dataset['Position:'].str.contains('Goalkeeper'), 1, 0)


In [79]:
# Creating the Column Age from current_date and birth
# date_birth_df =  dataset[~pd.isna(dataset['Date of Birth:'])][['FBRefID', 'Date of Birth:']].drop_duplicates()

# dataset = pd.merge(dataset.drop(columns=['Date of Birth:'], axis=1), date_birth_df, left_on='FBRefID', right_on='FBRefID', how='left')


# dataset['age'] = round((pd.to_datetime(dataset['agg_date']) - pd.to_datetime(dataset['Birth'])) / timedelta(days=365), 0)

# dataset[dataset['FBRefID'] == '71672fa0']

dataset[pd.isna(dataset['agg_date'])]

name   FBRefID  week    year Date  Min  Gls  Ast   PK  PKatt   Sh  \
117549   NaN  16b8fabd  29.0  2015.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
117580   NaN  16b8fabd   2.0  2016.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
117657   NaN  16b8fabd  28.0  2017.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
126545   NaN  09586899  13.0  2010.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
126933   NaN  09586899  51.0  2017.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
162107   NaN  73d9bdc7  51.0  2011.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
164199   NaN  362aa29d  51.0  2016.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
188667   NaN  5570e6fb  37.0  2021.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
189045   NaN  b7e7937d   3.0  2015.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
192689   NaN  2f90f6b8  10.0  2016.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
195559   NaN  5042e5c2   7.0  2015.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
202915   NaN  c9e99e49  44.0  2018.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
205693   NaN  c419e035  30.0  2009.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
236827   NaN  abb42ce6  33.0  2008.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
246305   NaN  43a1bea5  50.0  2014.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
248849   NaN  5370cba7  48.0  2017.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
252547   NaN  86015b20  39.0  2017.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
252640   NaN  86015b20  39.0  2020.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
252641   NaN  86015b20  40.0  2020.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
252642   NaN  86015b20  43.0  2020.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
255041   NaN  6ef56efd  16.0  2016.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
264603   NaN  defb905a   6.0  2019.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
264604   NaN  defb905a   6.0  2019.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
282187   NaN  b746d309  32.0  2015.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
283272   NaN  5f9f0531  14.0  2016.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
293074   NaN  d70ce98e  51.0  2015.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
301999   NaN  adfc9123  51.0  2016.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
308938   NaN  fb2a63bb  44.0  2013.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
314135   NaN  13d820de   6.0  2011.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
315392   NaN  f61c7c4e  37.0  2009.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
315416   NaN  f61c7c4e  40.0  2011.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
315424   NaN  f61c7c4e  34.0  2013.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
315487   NaN  f61c7c4e  49.0  2015.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
315507   NaN  f61c7c4e  20.0  2017.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
315509   NaN  f61c7c4e  37.0  2017.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
315519   NaN  f61c7c4e  11.0  2018.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
315521   NaN  f61c7c4e  38.0  2018.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
326858   NaN  f4ec4fd0  12.0  2018.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
328620   NaN  15e9c7e6  10.0  2015.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
330644   NaN  dba67bc4  44.0  2007.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
330675   NaN  dba67bc4  13.0  2011.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
330690   NaN  dba67bc4  43.0  2011.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
335471   NaN  4dba2a97  45.0  2019.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
335472   NaN  4dba2a97  48.0  2019.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
337098   NaN  d003e213  47.0  2017.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
337499   NaN  d3d758d8  11.0  2012.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
348190   NaN  27d2618c  29.0  2017.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
352478   NaN  b8673e18  11.0  2015.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
366466   NaN  e26c4233  12.0  2016.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
368034   NaN  f07be45a  40.0  2008.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
368063   NaN  f07be45a  38.0  2015.0  NaN  0.0  0.0  0.0  0.0    0.0  0.0   
3733

In [64]:
# Creating 'retired' dummy variable

dataset['retired'] = np.where(dataset['Retired since:'].isnull(), 0, 1)

In [65]:
dataset.head()

name   FBRefID  week    year        Date   Min  Gls  Ast   PK  \
0  Jens-Lehmann  d1ca1129  31.0  1991.0  1991-08-03  90.0  0.0  0.0  0.0   
1  Jens-Lehmann  d1ca1129  32.0  1991.0  1991-08-10  90.0  0.0  0.0  0.0   
2  Jens-Lehmann  d1ca1129  33.0  1991.0  1991-08-14  90.0  0.0  0.0  0.0   
3  Jens-Lehmann  d1ca1129  34.0  1991.0  1991-08-20  90.0  0.0  0.0  0.0   
4  Jens-Lehmann  d1ca1129  34.0  1991.0  1991-08-24  90.0  0.0  0.0  0.0   

   PKatt   Sh  SoT  CrdY  CrdR  Touches  Press  Tkl  Int  Blocks   xG  npxG  \
0    0.0  0.0  0.0   0.0   0.0      0.0    0.0  0.0  0.0     0.0  0.0   0.0   
1    0.0  0.0  0.0   0.0   0.0      0.0    0.0  0.0  0.0     0.0  0.0   0.0   
2    0.0  0.0  0.0   0.0   0.0      0.0    0.0  0.0  0.0     0.0  0.0   0.0   
3    0.0  0.0  0.0   0.0   0.0      0.0    0.0  0.0  0.0     0.0  0.0   0.0   
4    0.0  0.0  0.0   0.0   0.0      0.0    0.0  0.0  0.0     0.0  0.0   0.0   

    xA  SCA  GCA  Cmp  Att Prog  Carries  Prog.1  Succ  Att.1  Fls  Fld  Off  \
0  0.0  0.0  0.0  0.0  0.0  0.0      0.0     0.0   0.0    0.0  0.0  0.0  0.0   
1  0.0  0.0  0.0  0.0  0.0  0.0      0.0     0.0   0.0    0.0  0.0  0.0  0.0   
2  0.0  0.0  0.0  0.0  0.0  0.0      0.0     0.0   0.0    0.0  0.0  0.0  0.0   
3  0.0  0.0  0.0  0.0  0.0  0.0      0.0     0.0   0.0    0.0  0.0  0.0  0.0   
4  0.0  0.0  0.0  0.0  0.0  0.0      0.0     0.0   0.0    0.0  0.0  0.0  0.0   

   Crs  TklW   OG  PKwon  PKcon  Won  Loss  Draw  index Season Injury from  \
0  0.0   0.0  0.0    0.0    0.0  0.0   0.0   1.0    NaN    NaN    NaN  NaN   
1  0.0   0.0  0.0    0.0    0.0  0.0   1.0   0.0    NaN    NaN    NaN  NaN   
2  0.0   0.0  0.0    0.0    0.0  1.0   0.0   0.0    NaN    NaN    NaN  NaN   
3  0.0   0.0  0.0    0.0    0.0  0.0   1.0   0.0    NaN    NaN    NaN  NaN   
4  0.0   0.0  0.0    0.0    0.0  1.0   0.0   0.0    NaN    NaN    NaN  NaN   

  until Days Games missed  TMId TmPos  TMID PlayerName PlayerFullName  \
0   NaN  NaN          NaN   NaN   NaN   NaN        NaN            NaN   
1   NaN  NaN          NaN   NaN   NaN   NaN        NaN            NaN   
2   NaN  NaN          NaN   NaN   NaN   NaN        NaN            NaN   
3   NaN  NaN          NaN   NaN   NaN   NaN        NaN            NaN   
4   NaN  NaN          NaN   NaN   NaN   NaN        NaN            NaN   

  Nationality Photo Position  FootAbility InternationalReputation PlayerUrl  \
0         NaN   NaN      NaN          NaN                     NaN       NaN   
1         NaN   NaN      NaN          NaN                     NaN       NaN   
2         NaN   NaN      NaN          NaN                     NaN       NaN   
3         NaN   NaN      NaN          NaN                     NaN       NaN   
4         NaN   NaN      NaN          NaN                     NaN       NaN   

  Twitter Instagram Place of birth: Citizenship: Position: Contract expires:  \
0     NaN       NaN             NaN          NaN                         NaN   
1     NaN       NaN             NaN          NaN                         NaN   
2     NaN       NaN             NaN          NaN                         NaN   
3     NaN       NaN             NaN          NaN                         NaN   
4     NaN       NaN             NaN          NaN                         NaN   

  Former International: Caps/Goals: League level: Joined: Contract until:  \
0                   NaN         NaN           NaN     NaN             NaN   
1                   NaN         NaN           NaN     NaN             NaN   
2                   NaN         NaN           NaN     NaN             NaN   
3                   NaN         NaN           NaN     NaN             NaN   
4                   NaN         NaN           NaN     NaN             NaN   

  Last club: Most games for: Unknown since: Date of birth: Foot:  \
0        NaN             NaN            NaN            NaN   NaN   
1        NaN             NaN            NaN            NaN   NaN   
2        NaN             NaN            NaN            NaN   NaN   

In [66]:
# Getting features for modelling

dataset_for_model = dataset[['name', 'FBRefID', 'TMId', 'current_date', 'agg_week', 'agg_year', 'was_match', 'Min', 'Gls', 'Ast', 'PK', 'PKatt','Sh', \
    'SoT', 'CrdY', 'CrdR', 'Touches', 'Press', 'Tkl', 'Int', 'Blocks', 'xG', 'npxG', 'xA', 'SCA', 'Cmp', 'Att', 'Prog', 'Carries', 'Prog.1', \
    'Att.1', 'Fls', 'Fld', 'Off', 'Crs', 'TklW', 'OG', 'PKwon', 'PKcon', 'Won', 'Loss', 'Draw', 'Injury', 'injury_year', 'injury_week', \
    'release_week', 'Days', 'Games missed', 'attacker', 'midfielder', 'defender', 'goalkeeper', 'age', 'Height', 'Weight', 'Foot', 'FootAbility', \
    'Caps/Goals:', 'retired']]

In [21]:
# Sorting values in dataset_for_model

# dataset_for_model = dataset_for_model[dataset_for_model['year'] > 2016]
dataset_for_model_final = dataset_for_model.sort_values(['FBRefID', 'agg_year', 'agg_week'])

In [67]:
dataset_for_model_final.loc[~pd.isna(dataset_for_model_final['Injury']), 'injured'] = 1
dataset_for_model_final.loc[pd.isna(dataset_for_model_final['Injury']), 'injured'] = 0

dataset_for_model_final[dataset_for_model_final['FBRefID'] == '71672fa0'].head()


name   FBRefID  TMId current_date  agg_week  agg_year  was_match  \
322107  Petr-Cech  71672fa0   NaN          NaN      38.0    2001.0        1.0   
323250  Petr-Cech  71672fa0   NaN          NaN      39.0    2001.0        1.0   
324493  Petr-Cech  71672fa0   NaN          NaN      41.0    2001.0        1.0   
325518  Petr-Cech  71672fa0   NaN          NaN      42.0    2001.0        1.0   
326503  Petr-Cech  71672fa0   NaN          NaN      43.0    2001.0        1.0   

         Min  Gls  Ast   PK  PKatt   Sh  SoT  CrdY  CrdR  Touches  Press  Tkl  \
322107  90.0  0.0  0.0  0.0    0.0  0.0  0.0   0.0   0.0      0.0    0.0  0.0   
323250  90.0  0.0  0.0  0.0    0.0  0.0  0.0   0.0   0.0      0.0    0.0  0.0   
324493  90.0  0.0  0.0  0.0    0.0  0.0  0.0   0.0   0.0      0.0    0.0  0.0   
325518  90.0  0.0  0.0  0.0    0.0  0.0  0.0   0.0   0.0      0.0    0.0  0.0   
326503  90.0  0.0  0.0  0.0    0.0  0.0  0.0   0.0   0.0      0.0    0.0  0.0   

        Int  Blocks   xG  npxG   xA  SCA  Cmp  Att Prog  Carries  Prog.1  \
322107  0.0     0.0  0.0   0.0  0.0  0.0  0.0  0.0  0.0      0.0     0.0   
323250  0.0     0.0  0.0   0.0  0.0  0.0  0.0  0.0  0.0      0.0     0.0   
324493  0.0     0.0  0.0   0.0  0.0  0.0  0.0  0.0  0.0      0.0     0.0   
325518  0.0     0.0  0.0   0.0  0.0  0.0  0.0  0.0  0.0      0.0     0.0   
326503  0.0     0.0  0.0   0.0  0.0  0.0  0.0  0.0  0.0      0.0     0.0   

        Att.1  Fls  Fld  Off  Crs  TklW   OG  PKwon  PKcon  Won  Loss  Draw  \
322107    0.0  0.0  0.0  0.0  0.0   0.0  0.0    0.0    0.0  0.0   0.0   1.0   
323250    0.0  0.0  0.0  0.0  0.0   0.0  0.0    0.0    0.0  1.0   0.0   0.0   
324493    0.0  0.0  0.0  0.0  0.0   0.0  0.0    0.0    0.0  1.0   0.0   0.0   
325518    0.0  0.0  0.0  0.0  0.0   0.0  0.0    0.0    0.0  1.0   0.0   0.0   
326503    0.0  0.0  0.0  0.0  0.0   0.0  0.0    0.0    0.0  0.0   0.0   1.0   

       Injury  injury_year  injury_week  release_week Days Games missed  \
322107    NaN          NaN          NaN           NaN  NaN          NaN   
323250    NaN          NaN          NaN           NaN  NaN          NaN   
324493    NaN          NaN          NaN           NaN  NaN          NaN   
325518    NaN          NaN          NaN           NaN  NaN          NaN   
326503    NaN          NaN          NaN           NaN  NaN          NaN   

        attacker  midfielder  defender  goalkeeper  age  Height  Weight Foot  \
322107         0           0         0           0  NaN     NaN     NaN  NaN   
323250         0           0         0           0  NaN     NaN     NaN  NaN   
324493         0           0         0           0  NaN     NaN     NaN  NaN   
325518         0           0         0           0  NaN     NaN     NaN  NaN   
326503         0           0         0           0  NaN     NaN     NaN  NaN   

        FootAbility Caps/Goals:  retired  injured  
322107          NaN         NaN        0      0.0  
323250          NaN         NaN        0      0.0  
324493          NaN         NaN        0      0.0  
325518          NaN         NaN        0      0.0  
326503          NaN         NaN        0      0.0

In [46]:
len(dataset_for_model_final['FBRefID'].unique())

FBRefId  Height  Weight   Foot             Birth
0  3bb7b8b4   188.0    89.0   LEFT   August 17, 1993
1  31c69ef1   186.0    82.0  RIGHT      May 14, 1997
2  6434f10d   190.0    78.0  RIGHT     June 22, 1996
3  b400bde0   170.0    70.0  RIGHT  December 8, 1994
4  bd6351cd   182.0    66.0  RIGHT      May 27, 1994

1523614.0

In [297]:
# dataset_for_model_final[dataset_for_model_final['FBRefID'] == '71672fa0']

In [298]:
# Saving dataset_for_model_final to Google Drive

# Renzo's path
dataset_for_model_final.to_csv('/Volumes/GoogleDrive/.shortcut-targets-by-id/1KUGn_35OjAoOP2puz6yG-2g_8LBxvDG_/SIADS 697 - Capstone/Dataframes/dataset_for_model_final.csv', index=False)